In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
# !pip install kaleido
# home_dir = "/Users/weugene/"
a4width = 2480
a4height = 3508
figborderlinesize = 0.7
legborderlinesize = 0.7
pd.options.display.max_columns = None

In [109]:
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio
from pathlib import Path
import math 
from math import pi
from scipy.signal.windows import blackman # window function
from scipy.signal.windows import barthann
from scipy.signal.windows import chebwin
from scipy.fftpack import fft, fftfreq, ifft
from numpy.fft import irfft
import plotly
from scipy.optimize import curve_fit
plotly.io.orca.config.executable = '/Applications/orca.app/Contents/MacOS/orca'
plotly.io.orca.config.save()


theta_sym ='\u03B8'
delta_sym = '\u03B4'
Delta_sym = '\u0394'
Sigma_sym = '\u03A3'
omega_sym = '\u03C9'
hat_sym   = '\u0302' #symbol + hat_sym

def plot_graph(list_x_, list_y_, names, xtitle, ytitle, image_name, list_errors=None, add_error_bar=None, mode=['lines+markers']*20,
               xrange=[], yrange=[],
               dash=['solid', 'dot', 'dash', 'longdash'],
               colors=['blue', 'red', 'hsv(120,100,100)', 'green', 'black' ],
               marker_size=15, line_size=3,
               marker_style = ['circle' ]*20, #'triangle-up', 'triangle-down','square', 'diamond', 'cross',  'x-thin', 'cross-thin' 
               width=1000, height=500, path='./', xlog=False, ylog=False, 
               yanchor='top', y0_anchor=0.99, xanchor='right', x0_anchor=0.99, legend_orientation=None, showlegend=True,
               legborderlinesize=0.7, figborderlinesize=0.7, lmargin=0, rmargin=0, bmargin=0, tmargin=0, padmargin=0.1, debug=False,
               legendfont_size=18, tickfont_size=18, titlefont_size=20):

    list_x, list_y = [], []
    for i,x in enumerate(list_x_):
        y = list_y_[i]
        list_x.append(np.array(x))
        list_y.append(np.array(y))
    if mode == []:
        for i in range(len(list_x)):
            mode.append('lines+markers')
    if xrange == []:
        minx, maxx = [], []
        for i,x in enumerate(list_x):
            minx.append(x.min())
            maxx.append(x.max())
        xrange = [minx, maxx]
    if yrange == []:
        miny, maxy = [], []
        for i,y in enumerate(list_y):
            miny.append(y.min())
            maxy.append(y.max())
        yrange = [miny, maxy]

    axis_style = dict(showline=True, 
                  gridwidth=1, 
                  gridcolor='lightgrey', 
                  linewidth=2, 
                  linecolor='black', 
                  mirror=True, 
                  ticks='outside',
                  tickfont = dict(family = 'Times New Roman', 
                                  size = tickfont_size, 
                                  color = 'black'),
                  titlefont = dict(family = 'Times New Roman',
                                   size = titlefont_size,
                                   color = 'black'
              ))
    
    bg_style = {'plot_bgcolor': 'rgba(255, 255, 255, 1)', 'paper_bgcolor': 'rgba(255, 255, 255, 1)',}


    fig = go.Figure()
    for i,x in enumerate(list_x):
        if debug:
            print('curve number',i)        
        y = list_y[i]
        if list_errors!=None and add_error_bar[i]:
            fig.add_trace(go.Scatter(x=x, y=y, name=names[i],
                     error_y=dict(
                         type='data', # value of error bar given in data coordinates
                         array=list_errors[i],
                         visible=True),
                     mode=mode[i],
                     marker=dict(
                         size=marker_size,
                         line=dict(
                             color=colors[i],
                             width=1
                         )
                     ),
                     marker_symbol=marker_style[i],
                     line=dict(color=colors[i], width=line_size, dash=dash[i])))
        else:
            fig.add_trace(go.Scatter(x=x, y=y, name=names[i],
                     mode=mode[i],
                     marker=dict(
                         size=marker_size,
                         line=dict(
                             color=colors[i],
                             width=1
                         )
                     ),
                     marker_symbol=marker_style[i],
                     line=dict(color=colors[i], width=line_size, dash=dash[i])))
    fig.update_layout(
        width = width,
        height = height,
        xaxis_title=xtitle,
        yaxis_title=ytitle,
        showlegend=showlegend
    )
    fig.update_layout(bg_style)
    fig.update_xaxes(axis_style)
    fig.update_yaxes(axis_style)
    fig.update_layout(legend=dict(
        # yanchor="bottom",
        # y=0.1,
        # xanchor="left",
        # x=1.01,
        bgcolor="White",
        bordercolor="Black",
        borderwidth=figborderlinesize
    ))
    fig.update_layout(
        
        autosize=False,
        margin=dict(
            l=lmargin,
            r=rmargin,
            b=bmargin,
            t=tmargin,
            pad=padmargin
        ),
        #     paper_bgcolor="LightSteelBlue",
    )
    fig.update_yaxes(side='left',tickangle=0,automargin=True)
    fig.update_xaxes(side='bottom',tickangle=0,automargin=True)


    fig.update_layout(
        legend=dict(
        yanchor=yanchor,
        y=y0_anchor,
        xanchor=xanchor,
        x=x0_anchor,
            borderwidth=legborderlinesize
    ))
    fig.update_layout(
        font=dict(
            family="Times New Roman",
            size=legendfont_size
        )
    )
    if legend_orientation is not None:
        fig.update_layout(legend_orientation=legend_orientation)

    if xlog:
        fig.update_xaxes(type="log")
    if ylog:
        fig.update_yaxes(type="log")
    fig.update_xaxes(range=xrange)
    fig.update_yaxes(range=yrange)
    fig.show()
    fn = path + image_name
    pio.write_image(fig, str(Path(fn)))#, engine='kaleido'
    print("Successfully generated:", fn)





import itertools
import operator
from scipy.interpolate import interp1d

def monotone_increasing(lst):
    pairs = zip(lst, lst[1:])
    return all(itertools.starmap(operator.lt, pairs))

# def mean_value(x, y, tavg):
#     nan_num = np.isnan(x) + np.isnan(y)
#     if nan_num.sum() > 0:
#         print("Alert! there is nan in x, y array")
#         x = x[~nan_num]
#         y = y[~nan_num]
#     nan_num = np.isnan(x) + np.isnan(y)
#     if nan_num.sum() == 0:
#         print('Array is cleaned of Nan')

#     if tavg:
#         pass
#     else:
#         tavg = [np.min(x), np.max(x)]
#         print('tavg', tavg)
        
#     try:
#         sel = (x >= tavg[0]) & (x <= tavg[1])
#         xs = x[sel]
#         ys = y[sel]
#         T = xs.max() - xs.min()
#         print('T mean=', T)
#         ss = np.trapz(y=ys, x=xs)
#         f_mean = ss/T
#         print('ss=', ss, 'fmean=', f_mean)
#         return f_mean
#     except:
#         T = x.max() - x.min()
#         print('T mean=', T)
#         ss = np.trapz(y=y, x=x)
#         f_mean = ss/T
        
            
#         print('ss=', ss, 'fmean=', f_mean)
#         return f_mean

def mean_value(x, y, tavg=None, frac=0.8):
    nan_num = np.isnan(x) + np.isnan(y)
    if nan_num.sum() > 0:
        print("Alert! there is nan in x, y array")
        x = x[~nan_num]
        y = y[~nan_num]
    try:
        NT = int(frac*x.shape[0])
    except:
        NT = int(frac*len(x))
#     print('NT=', NT)
    x = x[NT:]
    y = y[NT:]

    if NT <2:
        print("NT too short")
        return None

    if tavg == None and frac == None:
        tavg = [np.min(x), np.max(x)]

    try:
        sel = (x >= tavg[0]) & (x <= tavg[1])
        xs = x[sel]
        ys = y[sel]
        T = xs.max() - xs.min()
        ss = np.trapz(y=ys, x=xs)
        f_mean = ss/T
        # Std calculation
        f_std = np.std(ys)
        print('tavg used: T mean=', T, 'ss=', ss, 'fmean=', f_mean)
        return [xs.min(), xs.max()], [f_mean, f_mean], f_std
    except:
        T = x.max() - x.min()
        ss = np.trapz(y=y, x=x)
        f_mean = ss/T    
        # Std calculation
        f_std = np.std(y)
        print('T mean=', T, 'ss=', ss, 'fmean=', f_mean)
        return [x.min(), x.max()], [f_mean, f_mean], f_std
    
def myfft(t_full, f_full, window=None, freqcut=None, num_output=False, filter_fun=None, Ntop=5):
    t = np.array(t_full)
    f = np.array(f_full)
    
    # Apply a window t,f array 
    if window != None and len(window) == 2:
        print("fourier window")
        ind = (t > window[0]) & (t < window[1])
        t = t[ind]
        f = f[ind]
        
    # Sample duration
    T = t[-1] - t[0]
    # Number of sample points
    N = t.shape[0]
    
    # Interpolate to uniform mesh
    fun = interp1d(t, f, kind='cubic')
    N = 10*N
    N_half = np.int(np.ceil(0.5*N))
    timestep = T/(N - 1)
    tr = np.linspace(t[0], t[-1], N)
    fr = fun(tr)
    
    # Choose a filter
    if filter_fun == None:
        w = np.ones(N)
    else:
        w = filter_fun(N)
    # Apply a filter to the signal
    fr *= w
    
    # Mean substraction
    dt = tr[1] - tr[0]
    ss = np.trapz(y=fr, x=tr)
    f_mean = ss/T
    fr -= f_mean
    
    print('f_mean=', f_mean, '1/(d*N)=', 1/(dt*N), 'handle freq=', (0.5/dt), 'N=', N)
    
    freq = 2*np.pi*fftfreq(N, dt) 
    if freqcut == None: # do not cut
        freqcut = [0, np.max(freq)]
    freq_num = np.arange(N_half)
    
    # FFT and power calculation
    sp = fft(fr)
    res = np.absolute(sp)**2
    freq = np.asarray(freq)
    
    # Calculation of threshold
    mask_threshold = (freq > freqcut[0]) & (freq < freqcut[1])
    res_cut = np.where(mask_threshold, res, 0)
    P_max = max(res_cut)
    sorted_ampl = sorted(res_cut)
    
    threshold = max(sorted_ampl[-Ntop], 0.2*P_max)
    mask_threshold = (res_cut >= threshold)
    print('the Nth big freq = ', freq[mask_threshold], ' P=', res[mask_threshold], 'threshold:', threshold)
    # Compressed data
    mask = (np.abs(freq) > freqcut[0]) & (np.abs(freq) < freqcut[1])
    sp_compressed = np.where(mask, sp, 0)
    
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=freq, y=res))
    fig.add_trace(go.Scatter(x=[freqcut[0], freqcut[0]], y=[0, max(res)]))
    fig.update_xaxes(range=[0,freqcut[1]])
    fig.show()
    
    Fmax = max(f_full)
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=t_full, y=f_full, name='original data'))
    fig.add_trace(go.Scatter(x=tr, y=fr, name='preprocessed data'))
    fig.add_trace(go.Scatter(x=tr, y=ifft(sp).real, name='Fourier data'))
    fig.add_trace(go.Scatter(x=tr, y=ifft(sp_compressed).real, name='Fourier compressed data'))
    fig.add_trace(go.Scatter(x=[t[0], t[0]], y=[0, Fmax]))
    fig.add_trace(go.Scatter(x=[t[-1], t[-1]], y=[0, Fmax]))
    fig.show()
    
#     plt.figure(figsize=(20,10))
#     plt.plot(t_full, f_full, 'b-', label='original data')
#     plt.plot(tr, fr, 'r.', label='preprocessed data')
#     plt.plot(tr, ifft(sp), 'g-', label='Fourier data')
#     plt.plot(tr, ifft(sp_compressed), 'k-', label='Fourier compressed data')
#     plt.legend()
#     plt.xlim([0,max(t_full)])
#     plt.show()
    
    freq, res = zip(*sorted(zip(freq, res)))
    freq = np.asarray(freq)
    mask = (np.abs(freq) > freqcut[0]) & (np.abs(freq) < freqcut[1])
    res = np.asarray(res)
    res = np.where(mask, res, 0)
    res = res/np.max(res)
    if num_output:
        return freq_num, res
    else:
        return freq, res
    
mode_lines_all=['lines']*20
mode_lines_and_markers_all=['lines+markers']*20

In [79]:
mu1 = 0.88e-3
mu2 = 0.019e-3
rho1 = 997
rho2 = 1.204
sigma = 72.8e-3
diam = 0.514e-3
# mu1 = 1e-3
# mu2 = 0.018e-3
# rho1 = 1000
# rho2 = 1.20
# sigma = 60e-3
# diam = 2.54e-2
U1 = 0
U2 = 1

path = '/Users/weugene/basilisk/work/tube/Contours_OpenFOAM_ANSYS_Experiment/'

In [315]:
from numpy import tanh 
from scipy.optimize import fmin, fsolve
from collections.abc import Iterable

coth = lambda x: 1.0/np.tanh(x)

def w_R(k, V, ind=1):
    res1 = -k**2*(mu1 + mu2)/(rho1 + rho2)
    res2 = rho1*rho2*k**2*(V)**2/(rho1 + rho2)**2 \
            - sigma*k**3/(rho1 + rho2) \
            + k**4*(mu1 + mu2)**2/(rho1 + rho2)**2
#     print(res1, res2)
    return res1 + ind*np.sqrt(res2)

# def w_cap(k, delta):
#     return np.sqrt((sigma/rho1)*k**3*np.tanh(k*delta))

def w_cap(k_wave, delta):
    res = []
    for i in range(len(k_wave)):
        k = k_wave[i]
        try:
            d = delta[i]*diam
        except:
            d = delta*diam
        res.append(np.sqrt((sigma/rho1)*k**3*np.tanh(k*d)))
    return np.asarray(res)

def k_cap(w, delta):
    res = []
    for i in range(len(w)):
        wave = w[i]
        try:
            d = delta[i]*diam
        except:
            d = delta*diam
        res.append(fsolve(w_cap, [2*np.pi/diam], args=(delta))[0])
    return np.asarray(res)

def w_I(k, ind=1):
    return -k*(rho1*U1 + rho2*U2)/(rho1 + rho2) 

def k_c(V, guess=1e-2, ind=1):
    if isinstance(V, Iterable):
        res = [None]*len(V)
        for i,v in enumerate(V):
            roots = fmin(lambda x: -w_R(x, v, ind), guess, disp=False)
            if len(roots)==1:
                res[i] = roots[0]
            else:
                print('Saved only one root:', roots)
                res[i] = roots[0]
    else:
        res = fmin(lambda x: -w_R(x, V, ind), guess, disp=False)
    return res

def V_comp(k):
    ha = 0.5
    h1 = (1-ha)*diam
    h2 = ha*diam
    
    res = (mu1*coth(k*h1) + mu2*coth(k*h2))**2*sigma*k/\
    (rho1*mu2**2*coth(k*h1)*coth(k*h2)**2 + rho2*mu1**2*coth(k*h1)**2*coth(k*h2))
    return np.sqrt(res)

# def w_max(V):
#     roots = fsolve(w_R, )

In [335]:
def find_w(k, delta, wave):
    res = w_cap(k, delta) - wave
#     print(res)
    return res

def k_cap(w, delta):
    res = []
    for i in range(len(w)):
        wave = w[i]
        try:
            d = delta[i]*diam
        except:
            d = delta*diam
        res.append(fsolve(find_w, [2*np.pi/diam], args=(d, wave))[0])
    return np.asarray(res)

ValueError: The array returned by a function changed size between calls

In [207]:
listV = [0.242, 0.666, 0.757, 1.118, 1.58, 2.06, 2.575, 3.09]
N = len(listV)
# k = np.linspace(1, 1e+4, 10000)
k = np.logspace(-3, 4, 10000)
listk = [k]*N
listwr = []
names = []
for v in listV:
    listwr.append(w_R(k, v, 1))
    names.append('V={:4}'.format(v))

/Users/weugene/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:13: RuntimeWarning:

invalid value encountered in sqrt



In [208]:
plot_graph(listk, listwr, names=names, xtitle='$k, \mathrm{m}^{-1}$', ytitle='$\omega_R$', image_name='w_vs_k.eps',
           xrange=[], yrange=[], mode=mode_lines_all,
           dash=['solid']*20, #, 'dot', 'dash', 'longdash'],
           colors=['blue', 'red', 'hsv(120,100,100)', 'green', 'black', 'hsv(120,100,0)', 'hsv(200,100,100)', 'hsv(100,100,200)' ],
           marker_size=0, line_size=3,
           marker_style = ['circle' ]*20,
           width=800, height=500, path=path, xlog=True, ylog=False, 
           yanchor='top', y0_anchor=0.99, xanchor='right', x0_anchor=0.99, legend_orientation=None, showlegend=True,
           legborderlinesize=0.7, figborderlinesize=0.7, lmargin=0, rmargin=0, bmargin=0, tmargin=0, padmargin=0.1, debug=False,
           legendfont_size=18, tickfont_size=18, titlefont_size=20)

Successfully generated: /Users/weugene/basilisk/work/tube/Contours_OpenFOAM_ANSYS_Experiment/w_vs_k.eps


In [ ]:
k = 100 = 2pi/lamda

In [338]:
6/100, 0.514e-3*30

(0.06, 0.015420000000000001)

In [209]:
V = [10,15]; k = 7e+4
k_c(V, ind=1)

[1097.6185625000007, 2465.604125000001]

In [210]:
listV_all = np.logspace(-3, 0.8, 1000)
listk_c = k_c(listV_all, ind=1)

names = ['$k_c$']
plot_graph([listV_all], [listk_c], names=names, xtitle='$V$', ytitle='$k_c$', image_name='k_c_vs_V.eps',
               xrange=[], yrange=[], mode=mode_lines_all,
               dash=['solid']*20, #, 'dot', 'dash', 'longdash'],
               colors=['blue', 'red', 'hsv(120,100,100)', 'green', 'black' ],
               marker_size=0, line_size=3,
               marker_style = ['circle' ]*20,
               width=800, height=500, path=path, xlog=False, ylog=False, 
               yanchor='top', y0_anchor=0.99, xanchor='right', x0_anchor=0.99, legend_orientation=None, showlegend=True,
               legborderlinesize=0.7, figborderlinesize=0.7, lmargin=0, rmargin=0, bmargin=0, tmargin=0, padmargin=0.1, debug=False,
               legendfont_size=18, tickfont_size=18, titlefont_size=20)

/Users/weugene/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:13: RuntimeWarning:

invalid value encountered in sqrt



Successfully generated: /Users/weugene/basilisk/work/tube/Contours_OpenFOAM_ANSYS_Experiment/k_c_vs_V.eps


In [15]:
k = np.linspace(1e-2, 40, 1000)
V = V_comp(k)

names = ['$V$']
plot_graph([k], [V], names=names, xtitle='$k$', ytitle='$V$', image_name='V_vs_k.eps',
               xrange=[], yrange=[], mode=mode_lines_all,
               dash=['solid', 'dot', 'dash', 'longdash'],
               colors=['blue', 'red', 'hsv(120,100,100)', 'green', 'black' ],
               marker_size=0, line_size=3,
               marker_style = ['circle' ]*20,
               width=1000, height=500, path=path, xlog=False, ylog=False, 
               yanchor='top', y0_anchor=0.99, xanchor='right', x0_anchor=0.99, legend_orientation=None, showlegend=True,
               legborderlinesize=0.7, figborderlinesize=0.7, lmargin=0, rmargin=0, bmargin=0, tmargin=0, padmargin=0.1, debug=False,
               legendfont_size=18, tickfont_size=18, titlefont_size=20)

Successfully generated: /Users/weugene/basilisk/work/tube/Contours_OpenFOAM_ANSYS_Experiment/V_vs_k.eps


In [211]:
rpath = '/Users/weugene/basilisk/work/tube/'

tab = pd.read_excel(rpath + '/delta_u_mean_stats.xlsx', sheet_name=None, header=0)
sheets = tab.keys()
kcolumns = ['k1', 'k2', 'k3', 'k4', 'k5']
lambdacolumns = ['lambda1', 'lambda2', 'lambda3', 'lambda4', 'lambda5']

In [292]:
df = tab['lambda_U']
lambda_concat = df[lambdacolumns].values
df['lambda'] = [np.asarray([x for x in lams if not np.isnan(x)]) for lams in lambda_concat]
df['k'] = 2*np.pi/(df['lambda']*diam)
for i in range(1,6):
    nlam = 'lambda' + str(i)
    lam = df[nlam]*diam
    k_wave = 2*np.pi/lam
#     print(lam, k_wave)
    nk = 'k' + str(i)
    df[nk] = k_wave
    nw = 'w_rt_hk' + str(i)
    df[nw] = w_R(k_wave, 0, 1)
    df['w_cap' + str(i)] = w_cap(df[nk], df['delta'])
    df['w_cap_inf' + str(i)] = w_cap(df[nk], 1e+3)
    df['']
    
df['w_cap'] = w_cap(df['k'], df['delta'])
df['w_cap_inf'] = w_cap(df['k'], 1e+3)

/Users/weugene/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:13: RuntimeWarning:

invalid value encountered in sqrt

/Users/weugene/anaconda3/lib/python3.7/site-packages/numpy/core/_asarray.py:102: VisibleDeprecationWarning:

Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.



In [70]:

kmin = min(df[kcolumns].min())
kmax = max(df[kcolumns].max())
print('kmin=', kmin, 'kmax=', kmax)

kmin= 15280.119910456195 kmax= 111037.29610650377


In [303]:
df[['case', 't', 'lambda', 'k1', 'w_cap', 'w_cap_inf']]

case         t                                             lambda  \
0   AW1   3.36075                               [0.7999999999999998]   
1   AW2  13.94950           [0.3941999999999979, 0.5005000000000024]   
2   AW2  10.31450            [0.4253999999999998, 0.432599999999999]   
3   AW3   5.00892           [0.3728100000000012, 0.4611099999999997]   
4   AW3   5.98823           [0.3924099999999999, 0.4512999999999998]   
5   AW3   8.49668         [0.39250000000000007, 0.43159999999999954]   
6   AW4   5.06499  [0.3869800000000012, 0.3624899999999993, 0.440...   
7   AW4   6.00146  [0.4016700000000011, 0.3477899999999998, 0.455...   
8   AW4   7.64009  [0.4311000000000007, 0.36739999999999995, 0.42...   
9   AW5   7.31703           [0.4929799999999993, 0.4477999999999991]   
10  AW5  10.01680          [0.5562000000000005, 0.42739999999999867]   
11  AW5  15.78000         [0.31560000000000343, 0.29609999999999914]   
12  AW5  19.18400          [0.37460000000000093, 0.2735999999999983]   
13  AW6   3.92000  [0.34494000000000025, 0.28622999999999976, 0.1...   
14  AW6   5.06290  [0.5141100000000005, 0.25704999999999956, 0.32...   
15  AW6  10.03000                                    [0.3, 0.3, 0.2]   
16  AW6  15.03570  [0.46270000000000167, 0.2643999999999984, 0.17...   
17  AW6  17.04530  [0.38189999999999813, 0.22769999999999868, 0.1...   

              k1                                              w_cap  \
0   15280.119910                                [5931.242351844224]   
1   31009.883126            [30151.83035104081, 18923.141537721032]   
2   28735.533447             [26002.41508699544, 25165.86337035458]   
3   32789.077354           [35135.834488950655, 23297.091134744223]   
4   31151.336430            [31839.01163443089, 24291.669636257328]   
5   31144.193448            [31824.948832919534, 26489.39579315869]   
6   31588.443662  [37970.40690848072, 42849.540389057256, 29753....   
7   30433.181289  [35427.04658084651, 46233.8244342902, 27967.72...   
8   28355.592504  [31033.865873378483, 41800.112487366954, 32417...   
9   24796.332363             [28358.05186278521, 33676.84454821486]   
10  21977.878332             [22771.58704397195, 36569.56239695128]   
11  38732.876833             [61476.83764954723, 68323.12990443545]   
12  32632.397032             [46000.24018155079, 77742.63228385792]   
13  35438.325298  [52952.20816482989, 72231.44408967256, 316081....   
14  23777.199293  [26286.053958773937, 85980.94522648005, 59098....   
15  40746.986428  [66865.68452379147, 66865.68452379147, 127693....   
16  26419.053228  [31771.639391313995, 82166.58801099139, 155204...   
17  32008.630344  [44496.28451226307, 104267.22635268129, 177101...   

                                            w_cap_inf  
0                                 [16140.17555015654]  
1                [46662.5324154915, 32616.4816553856]  
2            [41624.306056606285, 40589.477604737964]  
3             [50735.495355519255, 36883.86496610067]  
4              [46982.17684138319, 38093.00504846541]  
5              [46966.01829292072, 40730.62558753713]  
6   [47974.49966858217, 52917.48425307238, 39454.1...  
7   [45366.90375542203, 56307.67544200261, 37559.9...  
8   [40801.50664771768, 51860.23812693984, 42248.4...  
9              [33365.62649180547, 38540.47835238721]  
10            [27841.76463396787, 41332.479384476464]  
11            [65138.498389990804, 71677.95784224333]  
12            [50372.276081603704, 80699.17501615424]  
13  [57006.961827627914, 75417.21811070082, 316170...  
14  [31329.91072600274, 88616.95484530755, 62869.0...  
15  [70284.79014547248, 70284.79014547248, 129121....  
16  [36693.909482329356, 84947.58923083976, 156147...  
17  [48934.904712544485, 106291.53737352847, 17777...

In [290]:
grouped_cases = list(df.groupby('case')['w_cap'])
mean_w_cap = {}
for el in grouped_cases:
    case = el[0]
    df_loc = el[1]
    s = np.array([])
    for x in df_loc.values:
        s = np.concatenate((s, x), axis=None)
    m = s.mean()
    std = s.std(ddof=1)
    mean_w_cap.setdefault(case, (m, std) )
    
grouped_cases = list(df.groupby('case')['w_cap_inf'])
mean_w_cap_inf = {}
for el in grouped_cases:
    case = el[0]
    df_loc = el[1]
    s = np.array([])
    for x in df_loc.values:
        s = np.concatenate((s, x), axis=None)
    m = s.mean()
    std = s.std(ddof=1)
    mean_w_cap_inf.setdefault(case, (m, std) )

In [291]:
mean_w_cap, mean_w_cap_inf

({'AW1': (5931.242351844224, nan),
  'AW2': (25060.812586527965, 4636.346216509194),
  'AW3': (28812.99192007689, 4784.843436018947),
  'AW4': (36161.49358817399, 6425.514143631967),
  'AW5': (46864.860733914335, 20110.60942537517),
  'AW6': (95713.8801794392, 69775.18170431352)},
 {'AW1': (16140.17555015654, nan),
  'AW2': (40373.19943305534, 5811.896537201849),
  'AW3': (43398.53101532107, 5605.492440477843),
  'AW4': (46054.53232231506, 6594.474785371431),
  'AW5': (51121.03202407864, 19293.850056557214),
  'AW6': (98577.74729510867, 68389.47760651894)})

In [319]:
xz = np.array(df.groupby('case')['k1'].mean())
stdxz = np.array(df.groupby('case')['k1'].std(ddof=1))
delta =  np.array(df.groupby('case')['delta'].mean())
w_cap(xz, delta), stdxz

(array([ 5931.24235184, 28041.96007422, 32917.19260077, 34762.12548835,
        38691.25409723, 43705.59231317]),
 array([          nan, 1608.20808096,  947.61889507, 1638.20699361,
        7610.51608878, 6829.62390192]))

In [300]:
1608/28041

0.05734460254627153

In [ ]:
w_cap(df['k1'], delta)

In [306]:
w_cap([2*np.pi/(0.43*diam)], 0.0716)

array([36181.01527256])

In [310]:
df[['t','case','k1','k2', 'w_cap1']]

t case            k1        w_cap1
0    3.36075  AW1  15280.119910   5931.242352
1   13.94950  AW2  31009.883126  30151.830351
2   10.31450  AW2  28735.533447  26002.415087
3    5.00892  AW3  32789.077354  35135.834489
4    5.98823  AW3  31151.336430  31839.011634
5    8.49668  AW3  31144.193448  31824.948833
6    5.06499  AW4  31588.443662  37970.406908
7    6.00146  AW4  30433.181289  35427.046581
8    7.64009  AW4  28355.592504  31033.865873
9    7.31703  AW5  24796.332363  28358.051863
10  10.01680  AW5  21977.878332  22771.587044
11  15.78000  AW5  38732.876833  61476.837650
12  19.18400  AW5  32632.397032  46000.240182
13   3.92000  AW6  35438.325298  52952.208165
14   5.06290  AW6  23777.199293  26286.053959
15  10.03000  AW6  40746.986428  66865.684524
16  15.03570  AW6  26419.053228  31771.639391
17  17.04530  AW6  32008.630344  44496.284512

In [345]:
df[df['case']=='AW3']

case        t  lambda1  lambda2  lambda3  lambda4  lambda5         U  \
3  AW3  5.00892  0.37281  0.46111      NaN      NaN      NaN  0.111828   
4  AW3  5.98823  0.39241  0.45130      NaN      NaN      NaN  0.078110   
5  AW3  8.49668  0.39250  0.43160      NaN      NaN      NaN  0.085000   

    notes  delta                                      lambda  \
3  2 pits  0.031    [0.3728100000000012, 0.4611099999999997]   
4   2pits  0.031    [0.3924099999999999, 0.4512999999999998]   
5   2pits  0.031  [0.39250000000000007, 0.43159999999999954]   

                                         k            k1  w_rt_hk1  \
3  [32789.07735405411, 26510.151435373253]  32789.077354       NaN   
4  [31151.336429665287, 27086.40799549071]  31151.336430       NaN   
5  [31144.19344806357, 28322.743114840054]  31144.193448       NaN   

             k2  w_rt_hk2  k3  w_rt_hk3  k4  w_rt_hk4  k5  w_rt_hk5  \
3  26510.151435       NaN NaN       NaN NaN       NaN NaN       NaN   
4  27086.407995       NaN NaN       NaN NaN       NaN NaN       NaN   
5  28322.743115       NaN NaN       NaN NaN       NaN NaN       NaN   

                                      w_cap  \
3  [35135.834488950655, 23297.091134744223]   
4   [31839.01163443089, 24291.669636257328]   
5   [31824.948832919534, 26489.39579315869]   

                                 w_cap_inf        w_cap1    w_cap_inf1  \
3  [50735.495355519255, 36883.86496610067]  35135.834489  50735.495356   
4   [46982.17684138319, 38093.00504846541]  31839.011634  46982.176841   
5   [46966.01829292072, 40730.62558753713]  31824.948833  46966.018293   

         w_cap2    w_cap_inf2  w_cap3  w_cap_inf3  w_cap4  w_cap_inf4  w_cap5  \
3  23297.091135  36883.864966     NaN         NaN     NaN         NaN     NaN   
4  24291.669636  38093.005048     NaN         NaN     NaN         NaN     NaN   
5  26489.395793  40730.625588     NaN         NaN     NaN         NaN     NaN   

   w_cap_inf5  
3         NaN  
4         NaN  
5         NaN

In [ ]:
-10.81 12.28 15.64 12.2,29.85,24.42 32.12